In [ ]:
# Author: Jeremy Martinez
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from pandas_datareader import data as pdr
import yfinance as yf
from datetime import datetime, timedelta
import matplotlib.animation as animation

In [ ]:
# Function to get data
def get_data(stocks, start, end):
    data = yf.download(stocks, start=start, end=end)['Close']
    stock_returns = data.pct_change()
    mean_returns = stock_returns.mean()
    covariance_matrix = stock_returns.cov()
    return mean_returns, covariance_matrix

# function to get animation
def update(frame):
    ax.clear()
    ax.plot(sims[:, :frame])
    ax.set_ylabel("Total Amount")
    ax.set_xlabel("Days")
    ax.set_title("10k for 365 Days")
    ax.set_ylim(7500, 15000)

In [ ]:
# Override pandas datareader
yf.pdr_override()

# ETFs in our portfolio
stock_portfolio = ["VTI", "VEA", "VWO", "DGRO", "VTEB"]
endDate = datetime.now()
startDate = endDate - timedelta(days=300)

mean_returns, covariance_matrix = get_data(stock_portfolio, startDate, endDate)
w = np.random.random(len(mean_returns))
weights = w / np.sum(w)

In [ ]:
n = 100
time = 365

meanM = (np.full(shape=(time, len(weights)), fill_value=mean_returns)).T

sims = np.full(shape=(time, n), fill_value=0.0)

principal = 10000

for i in range(n):
    Z = np.random.normal(size=(time, len(weights)))
    L = np.linalg.cholesky(covariance_matrix)
    dailyReturns = meanM + np.inner(L, Z)
    sims[:,i] = np.cumprod(np.inner(weights, dailyReturns.T) + 1) * principal 

fig, ax = plt.subplots()
    
ani = animation.FuncAnimation(fig, update, frames=range(1, n), interval=100)
ani.save('animation6.mp4', writer='ffmpeg', fps=10)
plt.show()

In [ ]:
minVal = float("inf")
maxVal = -float("inf")
total = 0
count = 0
for lst in sims:
    for elem in lst:
        if elem > maxVal:
            maxVal = elem
        
        if elem < minVal:
            minVal = elem
        count += 1
        total += elem
average = total / count
print("10K + 365 Days Stats")
print("Min:", minVal, "Max:", maxVal, "Average:", average)